In [2]:
import pandas as pd
import numpy as np
import os
import time
import random
import gensim
import numpy as np
import os
import torch
from gensim.models import KeyedVectors
from matplotlib import pyplot as plt
from matplotlib.pyplot import figure

/home/fatma/.local/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
def get_mean_vector(model, words):
    # remove out-of-vocabulary words
    # words: target list words
    # returns average vector for all words in target list
    import numpy as np
    words = [word for word in words if word in model.index_to_key]
    if len(words) >= 1:
        return np.mean(model[words], axis=0)
    else:
        return []

def mdi(mean, gini, weight):
    exp1 =  np.power(mean,weight) 
    exp2 = np.power((1 - gini),1-weight)
    return exp1 * exp2

def get_similarity_Scores(v1,v2):
    from numpy import dot
    from numpy.linalg import norm
    return dot(v1,v2)/(norm(v1)*norm(v2))

def normalize_data(a):
    normalizded_a = []
    amin, amax = min(a), max(a)
    for i in a:
        normalizded_a.append((i-amin) / (amax-amin))
    return normalizded_a
    
def get_similarity_scores_between_target_words_and_attribute_words(model, attribute_words, target_words):
    
    similarity_scores_summary = {}
    words = []
    mean_sim_socres = []

    target_words = [word for word in target_words if word in model.index_to_key]
    attribute_words = [word for word in attribute_words if word in model.index_to_key]
    
    if len(target_words) >= 1 and len(attribute_words) >=1:
        for i in target_words:
            similarity_scores = []
            words.append(i)
            for j in attribute_words:
                cos_sim = get_similarity_Scores(model[i], model[j])
                similarity_scores.append(cos_sim)
            mean_sim_socres.append(np.mean(normalize_data(similarity_scores)))

    similarity_scores_summary["word"] = words
    similarity_scores_summary["mean_sim_score"] = mean_sim_socres
    return similarity_scores_summary

def get_similarity_scores_between_avergare_target_vector_and_attribute_words(model, att_words, target_vector):
    # remove out-of-vocabulary words
    # att_words: wors in the attribute list
    # target_vector: average vector of all words in target group
    similarity_scores_summary = {}
    words_list = []
    similarity_scores = []
    words = [word for word in att_words if word in model.index_to_key]
    print(len(words))
    if len(words) >= 1:
        for i in words:
            print(i)
            words_list.append(i)
            cos_sim = get_similarity_Scores(model[i], target_vector)
            similarity_scores.append(cos_sim)
    similarity_scores_summary["words"] = words_list
    similarity_scores_summary["cos_sim_scores"] = similarity_scores
    similarity_scores_summary["sim_score"] = normalize_data(similarity_scores)

    return similarity_scores_summary


## Read profane words

In [4]:
data_folder = "../../Data/"
embeddings_folder = data_folder+"/word embeddings/"
results_folder = "Results/ethnicity_similarities/glove-CC/"

In [5]:
profane_words = open(data_folder+"swear_words.txt").read().splitlines()

## read word embeddings

In [6]:
def get_google_news_embeddings(filename,binary=False):
    w2v_model = gensim.models.KeyedVectors.load_word2vec_format(filename, binary=binary)
    return w2v_model


## word similarity

In [11]:
# convert text to w2v
#from gensim.scripts.glove2word2vec import glove2word2vec
#GLOVE_DIR = embeddings_folder+"/Glove/glove.42B.300d.txt"
#w2v_file = embeddings_folder+"/Glove/glove_2_wv.42B.300d.txt"
#glove2word2vec(GLOVE_DIR, w2v_file)

<ipython-input-11-818550c8a9b2>:5: DeprecationWarning: Call to deprecated `glove2word2vec` (KeyedVectors.load_word2vec_format(.., binary=False, no_header=True) loads GLoVE text vectors.).
  glove2word2vec(GLOVE_DIR, w2v_file)


(1917494, 300)

In [12]:
glove_wk_model = get_google_news_embeddings(embeddings_folder+"/Glove/glove_2_wv.42B.300d.txt")

## similar words

In [13]:
glove_wk_model.most_similar("girl")

[('girls', 0.832965612411499),
 ('boy', 0.8255643844604492),
 ('woman', 0.7628219723701477),
 ('sexy', 0.7407581210136414),
 ('teen', 0.7375307083129883),
 ('cute', 0.709848165512085),
 ('kid', 0.702916145324707),
 ('she', 0.6881920695304871),
 ('boys', 0.685463547706604),
 ('mom', 0.682237982749939)]

In [14]:
glove_wk_model.most_similar("queer")

[('transgender', 0.6561397314071655),
 ('lgbt', 0.6400501728057861),
 ('feminist', 0.639255166053772),
 ('lgbtq', 0.6118794083595276),
 ('gay', 0.5933998823165894),
 ('glbt', 0.580180287361145),
 ('feminism', 0.5667135715484619),
 ('homosexual', 0.5596978664398193),
 ('sexuality', 0.5481082201004028),
 ('transgendered', 0.538183867931366)]

In [15]:
glove_wk_model.most_similar("queers")

[('homosexuals', 0.5475353002548218),
 ('homos', 0.5453768372535706),
 ('faggots', 0.5372999310493469),
 ('queer', 0.5284385681152344),
 ('gays', 0.5019721984863281),
 ('fags', 0.4976077675819397),
 ('feminists', 0.4726851284503937),
 ('punks', 0.47250357270240784),
 ('homophobes', 0.46867305040359497),
 ('rednecks', 0.46313270926475525)]

In [16]:
glove_wk_model.most_similar("immigrant")

[('immigrants', 0.8096836805343628),
 ('immigration', 0.6855248808860779),
 ('migrant', 0.6616494059562683),
 ('undocumented', 0.614592969417572),
 ('migrants', 0.6076695919036865),
 ('refugee', 0.6058462262153625),
 ('citizenship', 0.5691381096839905),
 ('working-class', 0.5453857183456421),
 ('citizens', 0.5427461862564087),
 ('hispanic', 0.5413182377815247)]

## minority and 
majority words

In [17]:
harmless_majority_words_clean = ["hetrosexual", "cisgender", "man","male","boy","son","father","husband","brother","white","caucasian",
                                 "european american","european", "norwegian", "canadian", "german", "australian", "english",
                                "french", "american", "swedish", "dutch"]

target_words = ["lesbian","gay","bisexual","transgender","tran","queer",
                "lgbt","lgbtq","homosexual", "woman", "female", "girl","wife","sister","daughter","mother", "non-binary",
               "african", "african american", "asian", "black", "hispanic", "latin", "mexican", "indian", "middle eastern",
                "arab"]

words = harmless_majority_words_clean + target_words

In [18]:
profane_vector = get_mean_vector(glove_wk_model, profane_words)
vec_majority_sim_dict = get_similarity_scores_between_avergare_target_vector_and_attribute_words(glove_wk_model, words, profane_vector)
pd.DataFrame(vec_majority_sim_dict).to_csv(results_folder+"_minority_and_majority_words_sim_to_profane_vector.csv")

46
hetrosexual
cisgender
man
male
boy
son
father
husband
brother
white
caucasian
european
norwegian
canadian
german
australian
english
french
american
swedish
dutch
lesbian
gay
bisexual
transgender
tran
queer
lgbt
lgbtq
homosexual
woman
female
girl
wife
sister
daughter
mother
non-binary
african
asian
black
hispanic
latin
mexican
indian
arab


In [19]:
figure(figsize=(25, 10), dpi=1200)
sorted_index = np.argsort(vec_majority_sim_dict["sim_score"])

x_axis = np.arange(len(vec_majority_sim_dict["words"]))
y_axis = [vec_majority_sim_dict["sim_score"][i] for i in sorted_index]
x_ticks = [vec_majority_sim_dict["words"][i] for i in sorted_index]
plt.bar(x_axis, y_axis)
plt.xticks(x_axis, x_ticks, fontsize=40, fontweight='bold', rotation=90)
plt.ylabel("similarity score", fontsize=40, fontweight='bold')
plt.yticks(np.arange(0.1,1.1,0.1),fontsize=40, fontweight='bold')
plt.savefig(results_folder+"similarity_score_of_minority_and_majority_words_to_profanity_vector.pdf", bbox_inches='tight')